In [1]:
import os
import csv
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.datasets import load_iris
from sklearn.feature_extraction.text import TfidfVectorizer
from keras.models import Sequential
from keras.layers import Dense
from keras.utils import to_categorical
import MeCab



### csvとして保存されている情報を持ってくる

In [2]:
code_and_return_and_contetn = pd.read_csv('../datasets/datasets_for_training.csv')
code_and_return_and_contetn
docs = code_and_return_and_contetn['経営方針'].tolist()
stock_return = code_and_return_and_contetn['return'].tolist()

In [3]:
code_and_return_and_contetn

経営方針   code    return
0     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在に...  77160  0.209313
1     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在に...  76090  0.377778
2     １ 【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在...  59650 -0.063342
3     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在に...  59460  0.282051
4     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末におい...  69770  0.145766
...                                                 ...    ...       ...
1049  １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、有価証券報告書提出日現...  72960  0.342813
1050  １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、有価証券報告書提出日現...  72960  0.342813
1051  １ 【経営方針、経営環境及び対処すべき課題等】当社および当社の子会社(以下「当社グループ」と...  37990 -0.030928
1052  １ 【経営方針、経営環境及び対処すべき課題等】当社および当社の子会社(以下「当社グループ」と...  37990 -0.030928
1053  １ 【経営方針、経営環境及び対処すべき課題等】当社および当社の子会社(以下「当社グループ」と...  37990 -0.030928

[1054 rows x 3 columns]

In [4]:
code_and_return_and_contetn = code_and_return_and_contetn.drop_duplicates(subset='code')

In [5]:
code_and_return_and_contetn

経営方針   code    return
0     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在に...  77160  0.209313
1     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在に...  76090  0.377778
2     １ 【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在...  59650 -0.063342
3     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在に...  59460  0.282051
4     １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末におい...  69770  0.145766
...                                                 ...    ...       ...
1039  １【経営方針、経営環境及び対処すべき課題等】当社グループの事業を取り巻く環境は、当面は新型コ...  25880 -0.051373
1042  １ 【経営方針、経営環境及び対処すべき課題等】(1) 経営方針①経営の基本方針当社は、ものづ...  72640  0.031760
1045  １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、当連結会計年度末現在に...  36040  0.127758
1048  １【経営方針、経営環境及び対処すべき課題等】文中の将来に関する事項は、有価証券報告書提出日現...  72960  0.342813
1051  １ 【経営方針、経営環境及び対処すべき課題等】当社および当社の子会社(以下「当社グループ」と...  37990 -0.030928

[567 rows x 3 columns]

### 分かち書きにする

In [99]:
processed_docs = []

for doc in docs:
    m = MeCab.Tagger("-Ochasen")

    # 形態素解析の結果を格納するリスト
    nouns = []

    # 形態素解析の結果を解析
    node = m.parse(doc).split("\n")
    for i in node:
        if i == "EOS" or i == "":
            continue
        else:
            chunk = i.split("\t")
            pos = chunk[3].split("-")[0]  # 品詞情報がある部分を取得
            if pos == "名詞":  # 名詞のみを取得
                nouns.append(chunk[0])

    nouns = " ".join(nouns)

    processed_docs.append(nouns)

print(processed_docs)

['１ 経営 方針 経営 環境 対処 課題 等 文中 将来 事項 連結 会計 年度 末 現在 当社 グループ 判断 もの ( 1 ) 会社 経営 基本 方針 当社 グループ 1930 年 創業 以来 90 年間 顧客 ニーズ 製品 開発 堅牢 優美 廉価 製品 づくり 社会 信頼 経営 基本 歯科 医療 分野 一般 産業 分野 ニーズ 的確 把握 製品 開発 国内 世界 135 ヵ国 以上 愛顧 品質 基本 方針 品質 一 基本 全員 参加 品質 管理 顧客 満足 信頼 1997 年 ISO 9001 ( 品質 マネジメント システム 国際 規格 ) 認証 取得 1999 年 ISO 14001 ( 環境 マネジメント システム 国際 規格 ) 認証 取得 社員 徹底 品質 保証 体制 顧客 満足 一 設計 開発 製造 サービス 体制 製品 生産 使用 廃棄 段階 地球 環境 配慮 欧州 廃棄 電気 電子 機器 WEEE 指令 電気 電子 機器 含有 特定 危険 物質 制限 ROHS 指令 適応 欧米 販売 サービス 強化 今後 世界 ナカニシ ブランド 力 アップ 邁進 ( 2 ) 目標 経営 指標 当社 グループ 売上 高 営業 利益 率 30 ％ 確保 経営 指標 目標 ひとつ 利益 率 維持 ため 市場 ニーズ 的確 製品 開発 上市 売上 高 拡大 一方 全社 的 生産 性 向上 コスト 削減 成長 持続 ( 3 ) 中長期 的 会社 経営 戦略 当社 グループ 歯科 製品 関連 事業 工業 製品 関連 事業 二 本 柱 開発 生産 販売 三位一体 体制 強化 継続 的 メディカル 関連 事業 歯科 事業 競争 力 開発 生産 能力 販売 拠点 活用 投資 採算 性 考慮 NSK ブランド 価値 向上 アフターサービス 体制 R & D 体制 強化 販売 拠点 増強 営業 人員 増強 R & D 要員 増強 生産 能力 増強 更 事業 規模 拡大 ( 4 ) 経営 環境 会社 対処 課題 今後 見通し 原油 はじめ 物価 高騰 半導体 部品 不足 等 不透明 経営 環境 予想 よう 経営 環境 中 当社 グループ 国内外 経済 動向 注視 グローバル 競争 体制 強固 もの 歯科 製品 関連 事業 先進 諸国 歯科 医療 分野 市場 ニーズ 予防 歯科 審

### 普通のtfidfを求める

In [109]:
# モデルの生成
vectorizer = TfidfVectorizer(smooth_idf = False)
 
# TF-IDFの計算
values = vectorizer.fit_transform(processed_docs).toarray()
 
# 特徴量ラベルの取得
words = vectorizer.get_feature_names()
 
 
#結果のプリント
print(values)
print(type(values))
print(values.shape)
print(words)
print(type(words))

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]
<class 'numpy.ndarray'>
(1054, 13705)
['00', '000', '0000', '0001', '000100', '00011', '00013', '000136', '00014', '000141', '000145', '000147', '00016', '000162', '000170', '000180', '000185', '00019', '0002', '000200', '00022', '00023', '00027', '0003', '00032', '000360', '000367', '0004', '00040', '000409', '00041', '00042', '00045', '000472', '00049', '0005', '000500', '00056', '0006', '00060', '0008', '000800', '00082', '001', '002', '003', '0030', '004', '006', '0083', '01', '010', '011', '0112', '012', '0122', '012274', '0132', '01341', '014', '0147', '015', '0151', '017', '018', '02', '020', '022', '023', '0242', '025', '026', '03', '030', '033', '033156', '034', '036', '037', '0377', '038', '04', '040', '042000221', '046', '0461', '047', '048', '049', '05', '050', '051', '052', '053', '059', '06', '06111', '0651', '066', '0

### 指定キーワード用にカスタマイズされたtfidfを求める。

In [110]:
# CSVファイルのパスを指定
input_dir = os.path.join("..", "datasets")
input_file = os.path.join(input_dir, "keywords_wordnet.csv") # keywords_mecabもしくはkeywords_wordnetを選ぶ

# CSVファイルを読み込み、リストに変換
keywords = []

with open(input_file, 'r', encoding='utf-8') as csvfile:
    reader = csv.reader(csvfile)
    for row in reader:
        keywords.append(row[0])

In [111]:
print(keywords)

['unfeigned', 'true', 'genuine', '真成', 'ピュア', '醇正', 'ピュアー', '本当', '真正', '純粋', '実直', '真実', '真誠', 'sincere', '真正直', '篤実', '篤厚', '実体', '摯実', '正直', '実らしい', '実直', 'honest', '正当', 'reliable', 'dependable', 'true', 'honest', '律儀', '真正直', '真面目', '真成', '廉直', '良心的', '慥か', '篤実', '堅い', '実法', '謹直', 'まじめ', '真直ぐ', '潔癖', '真率', '堅気', '真っ直', '真すぐ', '堅実', '忠直', '実体', '着実', 'もの堅い', '真っ直ぐ', '正直', '頼もしい', '実らしい', '清潔', '貞実', '直', '手丈夫', '真っすぐ', '廉潔', '律義', '物堅い', '実直', '真誠', '固い', '清廉', '正しい', '手堅い', '確か', 'faithful', '律儀', '篤実', '忠義', 'もの忠実やか', '忠直', '篤厚', '実体', 'もの堅い', '貞実', '忠誠', '律義', '物堅い', '忠実', 'honest', 'honorable', '真正直', '真面目', '真直ぐ', '真っ直', '真すぐ', '真っ直ぐ', '正直', '清潔', '真っすぐ', '真直']


In [112]:
tfidf_before_keywords = pd.DataFrame(values, columns=words)

tfidf = pd.DataFrame()

for col in keywords:
    if col in tfidf_before_keywords.columns:
        tfidf[col] = tfidf_before_keywords[col]
    else:
        tfidf[col] = 0

tfidf = tfidf.values
print(type(tfidf))
print(tfidf.shape)
tfidf[np.isnan(tfidf)] = 0

<class 'numpy.ndarray'>
(1054, 66)


### 株式の収益率を数値から上昇（１）or下降（0）に書き換える

In [115]:
# tf-idfで出力された行列は（１, n）。nはスクリーニングする企業の数と同値。

print(stock_return)

stock_return = [1 if i > 0 else 0 for i in stock_return]
stock_return = np.array(stock_return)

print(values.shape)
print(type(values))
print(len(stock_return))
print(type(stock_return))

print(stock_return)


[0.20931326434619, 0.3777777777777777, -0.0633423180592991, 0.282051282051282, 0.1457663451232583, 0.1067961165048543, 0.2228889841405915, 0.5273972602739726, 0.0841121495327102, -0.1647619047619047, 0.1454545454545454, 0.1543134872417983, -0.2014218009478673, -0.1140684410646387, -0.73224043715847, -0.0852713178294573, -0.047361299052774, 0.4527961515333734, 0.2207792207792207, -0.5572519083969466, 0.3039140445126631, 0.6424242424242425, -0.012962256957682, 0.1288135593220339, 0.0, -0.3243735763097949, -0.2394366197183098, 0.035264483627204, -0.0978540772532188, 0.1246575342465753, 0.1522727272727272, 0.0264462809917355, 0.3022222222222222, 0.1438004402054292, -0.1952095808383233, -0.1313448456305599, 0.387989931679252, 0.0, 0.0865051903114186, 0.1237113402061855, -0.0118343195266272, 0.1821127673363577, 0.151877133105802, 0.0285714285714285, 0.1427728613569321, -0.0489361702127659, 0.0639354438237119, -0.0615141955835962, 0.2850719424460431, 0.254724111866969, -0.3464519976147883, -0

### 最後の確認

In [ ]:
print(tfidf)
print(tfidf.shape)
print(stock_return)
print(len(stock_return))

NameError: name 'tfidf' is not defined

### モデリング

#### データセットの調整

In [120]:
# 入力値はtfidfとvaluesとstocke_return

df_tfidf = pd.DataFrame(values, index=stock_return)
df_tfidf_after_keyword = pd.DataFrame(tfidf, index=stock_return)


In [121]:
count_0 = len(df_tfidf[df_tfidf.index == 0])
count_1 = len(df_tfidf[df_tfidf.index == 1])

df_tfidf = pd.concat([df_tfidf.loc[1].head(count_0), df_tfidf.loc[0]])
df_tfidf_after_keyword = pd.concat([df_tfidf_after_keyword.loc[1].head(count_0), df_tfidf_after_keyword.loc[0]])

coordinated_values = df_tfidf.values
coordinated_tfidf = df_tfidf_after_keyword.values
coordinated_stock_return = df_tfidf.index.values
print(coordinated_values)

[[0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 ...
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]
 [0. 0. 0. ... 0. 0. 0.]]


#### 活性化関数と次元を総当たり的に調べる

In [ ]:
cols = ['middle_activation', 'output_activation', 'middle_dimension', 'loss', 'accuracy', 'prediction']
results_of_experiments_for_overlearning = pd.DataFrame(columns=cols)
results_of_experiments_for_overlearning

Empty DataFrame
Columns: [middle_activation, output_activation, middle_dimension, loss, accuracy, prediction]
Index: []

In [54]:
print(values)
print(values.shape)

[[0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 ...
 [0.         0.03034079 0.         ... 0.         0.         0.        ]
 [0.         0.03034079 0.         ... 0.         0.         0.        ]
 [0.         0.02468059 0.         ... 0.         0.         0.        ]]
(755, 12106)


In [ ]:
x = values
y = stock_return

# データを訓練用とテスト用に分割
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=0)

activations = ['softmax', 'sigmoid', 'relu', 'elu', 'softplus', 'softsign', 'tanh','hard_sigmoid']
dims = [4, 5, 6, 7, 8]

for middle_activation in activations:
    for output_activation in activations:
        for dim in dims:
            # モデルの定義
            model = Sequential()
            model.add(Dense(dim, input_dim=x.shape[1], activation=middle_activation))
            model.add(Dense(1, activation=output_activation))
            
            # モデルのコンパイル
            model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

            # 訓練
            model.fit(x_train, y_train, epochs=50, batch_size=10)

            # 評価
            loss, accuracy = model.evaluate(x_test, y_test)

            predictions = model.predict(x_test)
            predicted_labels = np.argmax(predictions, axis=1)

            results_of_experiments_for_overlearning.loc[len(results_of_experiments_for_overlearning.index)] = [
                middle_activation, output_activation, dim, loss, accuracy, predicted_labels
            ]


Epoch 1/50
85/85 [==============================] - 1s 3ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 2/50
85/85 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 3/50
85/85 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 4/50
85/85 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 5/50
85/85 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 6/50
85/85 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 7/50
85/85 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 8/50
85/85 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 9/50
85/85 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accuracy: 0.6916
Epoch 10/50
85/85 [==============================] - 0s 3ms/step - loss: 0.0000e+0

In [ ]:
results_of_experiments_for_overlearning
results_of_experiments_for_overlearning.to_csv('results_of_experiments_for_overlearning.csv', index=False)

In [ ]:
results_of_experiments_for_overlearning

middle_activation output_activation  middle_dimension          loss  \
0             softmax           softmax                 4  0.000000e+00   
1             softmax           softmax                 5  0.000000e+00   
2             softmax           sigmoid                 4  0.000000e+00   
3             softmax           sigmoid                 5  0.000000e+00   
4             sigmoid           softmax                 4  0.000000e+00   
..                ...               ...               ...           ...   
323      hard_sigmoid      hard_sigmoid                 4  7.175157e-08   
324      hard_sigmoid      hard_sigmoid                 5  7.175157e-08   
325      hard_sigmoid      hard_sigmoid                 6  7.175157e-08   
326      hard_sigmoid      hard_sigmoid                 7  7.175157e-08   
327      hard_sigmoid      hard_sigmoid                 8  7.175157e-08   

     accuracy                                         prediction  
0    0.601896  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1    0.601896  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
2    0.398104  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
3    0.398104  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4    0.601896  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
..        ...                                                ...  
323  0.398104  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
324  0.601896  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
325  0.601896  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
326  0.601896  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
327  0.398104  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  

[328 rows x 6 columns]

#### 上の総当たり的な学習に対して、普通な一回限りの学習

In [118]:
print(values.shape)
print(len(stock_return))
print(tfidf.shape)

(1054, 13705)
1054
(1054, 66)


In [122]:
print(coordinated_values.shape)
print(coordinated_tfidf.shape)
print(len(coordinated_stock_return))

(688, 13705)
(688, 66)
688


In [124]:
# 例として、ランダムなデータを生成します。
# 実際には、具体的なデータセットに置き換えてください。
x = coordinated_tfidf
y = coordinated_stock_return

print(type(x))

# データを訓練用とテスト用に分割
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2, random_state=0)

# モデルの定義
model = Sequential()
model.add(Dense(8, input_dim=x.shape[1], activation='sigmoid'))
model.add(Dense(1, activation='sigmoid'))  # 出力層　回帰では恒等関数、２クラス分類ではシグモイド、多クラス分類ではソフトマックス

# モデルのコンパイル
model.compile(loss='categorical_crossentropy', optimizer='adam', metrics=['accuracy'])

# 訓練
model.fit(x_train, y_train, epochs=50, batch_size=10)

# 評価
loss, accuracy = model.evaluate(x_test, y_test)
print("Loss: ", loss)
print("Accuracy: ", accuracy)

predictions = model.predict(x_test)
predicted_labels = np.argmax(predictions, axis=1)
print(predicted_labels)

<class 'numpy.ndarray'>
Epoch 1/50
55/55 [==============================] - 6s 3ms/step - loss: 0.0000e+00 - accuracy: 0.4982
Epoch 2/50
55/55 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 3/50
55/55 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 4/50
55/55 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 5/50
55/55 [==============================] - 0s 4ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 6/50
55/55 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 7/50
55/55 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 8/50
55/55 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 9/50
55/55 [==============================] - 0s 3ms/step - loss: 0.0000e+00 - accuracy: 0.5036
Epoch 10/50
55/55 [==============================] - 0s 2m

### モデルが完成したので、そのモデルを用いて予測する作業

#### csvとして保存されている必要なものを持ってくる

In [ ]:
all_tosho_reports = pd.read_csv('../datasets/datasets_for_predicting.csv')
all_tosho_reports
all_docs = all_tosho_reports['経営方針'].tolist()

#### 分かち書き状態にする

In [ ]:
all_processed_docs = []

for doc in all_docs:
    m = MeCab.Tagger("-Ochasen")

    # 形態素解析の結果を格納するリスト
    nouns = []

    # 形態素解析の結果を解析
    node = m.parse(doc).split("\n")
    for i in node:
        if i == "EOS" or i == "":
            continue
        else:
            chunk = i.split("\t")
            pos = chunk[3].split("-")[0]  # 品詞情報がある部分を取得
            if pos == "名詞":  # 名詞のみを取得
                nouns.append(chunk[0])

    nouns = " ".join(nouns)

    all_processed_docs.append(nouns)

#### 普通のtfidf値を計算する

In [ ]:
 # TF-IDFの計算
all_values = vectorizer.fit_transform(all_processed_docs).toarray()
 
# 特徴量ラベルの取得
all_words = vectorizer.get_feature_names()

In [ ]:
all_tfidf_before_keywords = pd.DataFrame(all_values, columns=all_words)

all_tfidf = pd.DataFrame()

for col in keywords:
    if col in all_tfidf_before_keywords.columns:
        all_tfidf[col] = all_tfidf_before_keywords[col]
    else:
        all_tfidf[col] = 0

all_tfidf = all_tfidf.values
print(type(all_tfidf))
print(all_tfidf.shape)
all_tfidf[np.isnan(all_tfidf)] = 0

<ipython-input-25-b85e4f8a6ead>:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_tfidf[col] = 0
<ipython-input-25-b85e4f8a6ead>:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_tfidf[col] = all_tfidf_before_keywords[col]
<ipython-input-25-b85e4f8a6ead>:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.c

<class 'numpy.ndarray'>
(2555, 308)


<ipython-input-25-b85e4f8a6ead>:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_tfidf[col] = all_tfidf_before_keywords[col]
<ipython-input-25-b85e4f8a6ead>:7: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  all_tfidf[col] = all_tfidf_before_keywords[col]
<ipython-input-25-b85e4f8a6ead>:9: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented f

#### 最後の確認

In [ ]:
print(all_tfidf)
print(all_tfidf.shape)

[[0.         0.12040859 0.01018721 ... 0.         0.         0.        ]
 [0.         0.         0.         ... 0.         0.         0.        ]
 [0.         0.10395364 0.02418635 ... 0.03544617 0.         0.        ]
 ...
 [0.         0.04983905 0.         ... 0.         0.         0.        ]
 [0.         0.16336723 0.         ... 0.         0.         0.        ]
 [0.         0.03330216 0.06198592 ... 0.         0.         0.        ]]
(2555, 308)


In [ ]:
# 新しいデータセットで予測を行う
new_data = all_tfidf # ここに新しいデータセットを代入
predictions = model.predict(new_data)

# 予測結果を表示
print(predictions)
print(predictions.shape)

80/80 [==============================] - 0s 3ms/step
[[9.9997121e-01]
 [9.9975640e-01]
 [9.9991500e-01]
 ...
 [4.4032140e-04]
 [2.1889625e-06]
 [9.8995835e-01]]
(2555, 1)


In [ ]:
predicted_labels = np.argmax(predictions, axis=1)
results = predicted_labels.tolist()
print(predicted_labels)
print(type(predicted_labels))
print(len(predicted_labels))
print(results)

[0 0 0 ... 0 0 0]
<class 'numpy.ndarray'>
2555
[0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0